<a href="https://colab.research.google.com/github/haydenclose/Cloud_based_Oil_Detection/blob/main/Cloud_Based_Analysis_of_Oil_Spills_from_Wrecks.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Cloud Based Analysis of Oil Spills from Wrecks
This is a workflow on how to use Google Earth Engine (GEE) with Google Colab to identify and detect oil from shipwreck

Created By Hayden Close
First of all connect your google drive account with colab so you can store inputs such as wreck locations (detailed later) and even store things there.

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


# 1 Set-up of workspace
Import Earth Engine API (`import ee`).
Additionally, import useful python packages from examplar scripts (need to remove redundant ones after)

In [ ]:
import ee
!pip install geemap
import geemap
!pip install geopandas
import geopandas
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd                                                             # Useful package to read in csv's etc...
from scipy.stats import norm, gamma, f, chi2
import IPython.display as disp
%matplotlib inline
import ipyleaflet
import ipywidgets as widgets

Run the `ee.Authenticate` function to authenticate your access to Earth Engine servers and `ee.Initialize` to initialize it. Upon running the following cell you'll be asked to grant Earth Engine access to your Google account. Follow the instructions printed to the cell. Authorisation last a week but sometimes need doing again if refreshed.

In [3]:
# Trigger the authentication flow.. Only need to do once a week
ee.Authenticate()

# Initialize the library
ee.Initialize()

To authorize access needed by Earth Engine, open the following URL in a web browser and follow the instructions. If the web browser does not start automatically, please manually browse the URL below.

    https://code.earthengine.google.com/client-auth?scopes=https%3A//www.googleapis.com/auth/earthengine%20https%3A//www.googleapis.com/auth/devstorage.full_control&request_id=Gmb_jkKU55q3LXxS6XBn5TAM3ZXDMjPYfMe3tYgSNWc&tc=mgDF0JcChcGUKxmnEOWJVupMm6q_0oCjMYtHsUkso-8&cc=ir14cAarRZ3cLTeJmX9C2lh_MBrCOFtYYtVmU1_OI9E

The authorization workflow will generate a code, which you should paste in the box below.
Enter verification code: 4/1AbUR2VOqjdkwfZJ5qom-6L0qZBEdZwqQ05LAb122IhjBaZQtoIUXVoBP180

Successfully saved authorization token.


# 2 Interactive Maps

## 2.1 Manual creation of maps using Folium package

The [`folium`](https://python-visualization.github.io/folium/)
library can be used to display `ee.Image` objects on an interactive
[Leaflet](https://leafletjs.com/) map. Folium has no default
method for handling tiles from Earth Engine, so one must be defined
and added to the `folium.Map` module before use.

The following cell provides an example of adding a method for handing Earth Engine
tiles and using it to display an elevation model to a Leaflet map.

In [4]:
# Import the Folium library.
import folium                                                                   # Used for Interactive mapping

# Define a method for displaying Earth Engine image tiles to folium map.
def add_ee_layer(self, ee_image_object, vis_params, name):                      # Define function and variables
  map_id_dict = ee.Image(ee_image_object).getMapId(vis_params)                  # Method to display the  map
  folium.raster_layers.TileLayer(                                               # Add one of the mase maps and add options below
    tiles = map_id_dict['tile_fetcher'].url_format,                             # Not sure what this particularly does
    attr = 'Map Data &copy; <a href="https://earthengine.google.com/">Google Earth Engine</a>', # or what this does
    name = name,                                                                # Adds the layer name to the radio buttons rather than web address
    overlay = True,                                                             # Allow layers to overlay upon each
    control = True                                                              # Allows the user to turn on and off layers
  ).add_to(self)                                                                # Allows layers to be added after this base layer

# Add EE drawing method to folium, to be able to add other layers to this base map (see examplar below)
folium.Map.add_ee_layer = add_ee_layer                                         

from folium.plugins import Draw                                                 # Toolbox for adding the toolbar
draw = Draw(export=True)                                                        # Adds toolbars to folium plots

print('This sets up the base parameters of the map with no output.')             # Prints a statement so you know its ran


This sets up the base parameters of the map with no output


Now lets make an examplar interactive map just with the base layer.

In [ ]:
lat, lon = 52, 0                                                                # Define the Lat and Lon to centre the map on (UK)
my_map = folium.Map(location=[lat, lon], zoom_start=7)                          # Create the map zoomed to level 7 on our defined Lat and Lon (not yet ouputted)
draw.add_to(my_map)                                                             # Add the draw toolbar to the map
display(my_map)                                                                 # Display the map

## 2.3 Annotating map with points
There is a list of wreck locations (stored on sharePoint under 'Data for Google Colab'). I have uploaded the file called 'Wreck Database_V2.2.xls' to my google drive, you will need to do the same or you can use the navigation panel to the left `<-` click the folder icon and then upload a file (first icon along the top) but this will only be kept for an active session so will need to be uploaded each time. 

Now we use pandas to read the excel file and the `Wreck.head()` to view the first few rows of the dataframe. Note the ***magic wand*** button that allows for the interaction with the data.



In [ ]:
Wrecks = pd.read_excel('/content/drive/MyDrive/Wreck Database_V2.3.xls')      # Loads the xls file from your personal google drive
Wrecks.head()                                                                   # Displays the data to interact with

Owner             Wreck_ID Catergory   Latitude   Longitude  \
0   MOD           SS DERBENT  Priority  53.473390   -4.235660   
1   MOD  HMS PRINCE OF WALES  Priority   3.517583  104.464383   
2   MOD          HMS REPULSE  Priority   3.620619  104.345181   
3   MOD       RFA WAR MEHTAR  Priority  52.605000    2.148330   
4   MOD       RFA ATHELSTANE  Priority   7.332520   81.939600   

                                       Depth                            Cargo  
0                                        45m            3700 tons of fuel oil  
1                                       ~68m                              NaN  
2                                       ~68m                              NaN  
3  Between 26.5 m and 40 m with 2-3 m scour.  7000 tonnes Admiralty fuel oil   
4                                        42m  6096 tonnes Admiralty fuel oil

### 2.31 Adding the wrecks to the map
Here I use a little `for` loop to go through each row of the wreck dataframe and catergorise by priority.

This method also adds the wrecks to the `Folium.FeatureGroup`  so we can turn on and off the wrecks we do and dont want in the feature control panel.

Finally we can add a `popup`, this can be an extensive table but for now to keep it simple i have just added the wrecks name.

In [ ]:
Point_map = folium.Map(location=[lat, lon], zoom_start=7)                       # Base map with zoomed location and level.
for Wreck_group, Wreck in Wrecks.groupby('Catergory'):                          # For loop to group the wrecks together by priority
    feature_group = folium.FeatureGroup(Wreck_group)                            # Add the wreck groups to the feature control panel
    for row in Wreck.itertuples():                                              # Loop through the individual wrecks to plot
        folium.CircleMarker(location=[row.Latitude, row.Longitude],             # Adds circle marker by lat and long
                            popup=row.Wreck_ID,                                 # If click a point, tells us the name of the wreck
                            radius = 3,                                         # Size of point
                            fill_opacity=1).add_to(feature_group)               # Colour of outline by catergory
    feature_group.add_to(Point_map)                                             # Adds the points to the map 

folium.LayerControl().add_to(Point_map)                                         # Add the layer control to the map
Point_map                                                                       # Plots the map

## 2.4 Using interactive geemap
The above is a long winded process and extensive code. Fortunately there an amazing package called `geemap` that wraps up alot of different functions  based on the previous `folium` package and leaflet into nice interactive mapping utility. Notice the below the one simple line to create everthing and the toolbox allows for interactive changes to the base map etc... without hard coding it.

See below for the basic output and explanation

*   Has tool bar on the left that can search by name/address, lat-lon or data
*   Draw toolbar to add polygons, points etc...
*   On the right have a little spanner that has a lot of useful tools see https://geemap.org/
*   At the top if click the symbol next to the spanner can toggle layers on and off and adjust transparency

**I will be using  `geemap` from here onwards but can default back `folium` to customise ourselves if it is required**






In [ ]:
BasicMap = geemap.Map()                                                         # Basic interactive map with no added data
BasicMap                                                                        # Display the basic map

### 2.41 Add Points to geemap

Adds points from a dataframe with a simple piece of code `Map.add_points_from_xy(df, x="", y="")`

This also add the data as a popup when clicked
 
**NOTE. Found a little bug, need to load the wreck data in each time a map is called otherwise duplicate information is in the wreck popup** 

In [ ]:
PointsGeeMap = geemap.Map()                                                     # Basic map to draw onto
Wrecks = pd.read_excel('/content/drive/MyDrive/Wreck Database_V2.3.xls')        # Loads the xls file from your personal google drive
PointsGeeMap.add_points_from_xy(Wrecks, x="Longitude", y="Latitude")            # Simple line to add data (note can click the points for popup of data)
PointsGeeMap                                                                    # Displays the map

### 2.42 Sentinel-1 imagery example
Example from https://developers.google.com/earth-engine/datasets/catalog/COPERNICUS_S1_GRD

note this uses the `VV` band and `IW` instrument mode. Additionally, it creates a mean from the different months to identify change. 

Ideally we just need to look at one timestamp as the oil slicks will move with the tide (if any). Note the data is missing for the area of interest of Maylasia for the HMS Repulse and Prince of Wales.

In [ ]:
Wrecks = pd.read_excel('/content/drive/MyDrive/Wreck Database_V2.3.xls')       
SentExampleMap = geemap.Map()
imgVV = ee.ImageCollection('COPERNICUS/S1_GRD') \
        .filter(ee.Filter.listContains('transmitterReceiverPolarisation', 'VV')) \
        .filter(ee.Filter.eq('instrumentMode', 'IW')) \
        .select('VV')

def func_skh(image):
          edge = image.lt(-30.0)
          maskedImage = image.mask().And(edge.Not())
          return image.updateMask(maskedImage) \
        .map(func_skh)

desc = imgVV.filter(ee.Filter.eq('orbitProperties_pass', 'DESCENDING'))
asc = imgVV.filter(ee.Filter.eq('orbitProperties_pass', 'ASCENDING'))

spring = ee.Filter.date('2015-03-01', '2016-05-20')
lateSpring = ee.Filter.date('2015-04-21', '2016-05-10')
summer = ee.Filter.date('2015-06-11', '2016-08-31')

descChange = ee.Image.cat(
        desc.filter(spring).mean(),
        desc.filter(lateSpring).mean(),
        desc.filter(summer).mean())

ascChange = ee.Image.cat(
        asc.filter(spring).mean(),
        asc.filter(lateSpring).mean(),
        asc.filter(summer).mean())

SentExampleMap.setCenter(104.3, 3.6, 10)
SentExampleMap.addLayer(ascChange, {'min': -25, 'max': 5}, 'Multi-T Mean ASC', True)
SentExampleMap.addLayer(descChange, {'min': -25, 'max': 5}, 'Multi-T Mean DESC', True)
SentExampleMap.add_points_from_xy(Wrecks, x="Longitude", y="Latitude")  
SentExampleMap

#3 Find out which orbits and flights paths cover our Area of Interest (AoI)



### 3.1 **HMS REPULSE** and **HMS PRINCE OF WALES** just of Malaysia.

Found this useful bit of code to identify orbit passes over the Area of Interest and whether it is Ascending or Descending. Note for Malaysia it is quite simple but for Northwest Europe where coverage more extensive this is useful to find the orbits and related images that provide best coverage for our AoI.

In [12]:
OrbitsMap = geemap.Map()                                                                            # Base map

# Area of Interest of Malaysia
geometry = ee.Geometry.Polygon(
  [[[104.5, 3.5],
   [104.5, 3.5],
   [104.5, 3.7],
   [104.3, 3.7],
   [104.3, 3.5]]], None, False)


# Get Sentinel-1 data for an arbitrary 12 day period
s1 = (ee.ImageCollection('COPERNICUS/S1_GRD').                                                      # Selects the Sentinel 1 image collection   
  filterDate('2014-04-03', '2023-05-29').                                                           # Selects only the dates we are interested in
  filterMetadata('instrumentMode', 'equals', 'IW').                                                 # Selects the instrument mode that we wont
  filterBounds(geometry))                                                                           # Selects only images that our AoI is contained within

# This function gets the relative orbits to be able to plot them
def func_xmf(f):                                                                                    # Function definition
  return f.set('platform_relorbit',                                                                 # Full description i.e. 'A_18_Descending'
    ee.String(f.get('platform_number')).cat('_').                                                   # Determine whether A or B satelite
    cat(ee.Number(f.get('relativeOrbitNumber_start')).format('%.0f')).                              # Start number of orbit i.e. 18
    cat('_').cat(f.get('orbitProperties_pass')))                                                    # determines whether satelite ascending or descending

s1 = s1.map(func_xmf)                                                                               # Extracts the relative orbits from the image collection
orbits = ee.Dictionary(s1.aggregate_histogram('platform_relorbit'))                                 # Check which sensor/relative orbit combinations we have
keys = orbits.getInfo()                                                                             # Needed to loop

for k in keys:                                                                                      # Colours the orbits,
  color = 'blue'                                                                                    # Blue = A
  if (k[0]=='B'):                                                                                   # If orbit info [0] = B then colours it
    color = 'green'                                                                                 # Green = B
  
  OrbitsMap.addLayer(ee.Image().paint(ee.FeatureCollection(s1).                                     # Add outline of image 
    filterMetadata('platform_relorbit', 'equals', k), 0, 1),                                        # extract the name for the orbit, 0, 1 = position of  A or B in the string 
    {'palette': [color]}, 'Img' + k, True)                                                          # Changes the colour and adds the name to the layer feature group

for k in keys:                                                                                      # For all images
  OrbitsMap.addLayer(s1.filterMetadata('platform_relorbit', 'equals', k).first(),                   # Add the relative orbit again
    {'bands': ['angle'], 'min': 30, 'max': 45}, 'Incidence angle: ' + k, False)                     # Plot the angle of the receiving signal. True/False whether to display or not

OrbitsMap.addLayer(ee.Image().paint(geometry, 0, 1), {'palette': ['red']}, 'AOI', True)             # Adds the area of interest to the map
OrbitsMap.centerObject(geometry, 6)                                                                 # Centerss the map 
Wrecks = pd.read_excel('/content/drive/MyDrive/Wreck Database_V2.3.xls')                            # Loads the xls file from your personal google drive
OrbitsMap.add_points_from_xy(Wrecks, x="Longitude", y="Latitude")                                   # Adds the points to the map
OrbitsMap                                                                                           # Displays the map


Map(center=[3.599998163557322, 104.39999999999922], controls=(WidgetControl(options=['position', 'transparent_…

### 3.12 Orbit paths
Once run you can see that there is two orbit paths 18 Descending and 99 Ascending. However if you play with the dates then the earliest images come from orbit 18. Also notice how the position of the images changes over time.

# 4 Adding a single Sentinel-1 Image and detecting oil
So there is images available as identified from Section 3. Using the code below after the ImageCollection has been defined and ran (here I specified dates) by simplely typing `s1` it will provide a drop down menu and that can be explored. I.e. look at the dates to narrow down the image required.

In [11]:
# Get Sentinel-1 data for an arbitrary 12 day period
s1 = (ee.ImageCollection('COPERNICUS/S1_GRD').                                                      # Selects the Sentinel 1 image collection   
  filterDate('2014-04-03', '2023-05-29').                                                           # Selects only the dates we are interested in
  filterMetadata('instrumentMode', 'equals', 'IW').                                                 # Selects the instrument mode that we wont
  filterBounds(geometry))                                                                           # Selects only images that our AoI is contained within

s1                                                                                                  # Explore image collection

## 4.1 Extracting an single image from an `ImageCollection`

To extract the first image, add all the images` toList(99999)` with the number specifing the maximum number of images (used a very large number). Afterwards, `get(1)` selects the first image in the `ImageCollection` and select the `VV` band. Other bands are available but not appropiate for this study, see [Sentinel-1 dataset](https://developers.google.com/earth-engine/datasets/catalog/COPERNICUS_S1_GRD) for descriptions and how to use them.

Notice how we have one image and 1 band compared to 365 images with threee bands each.

In [14]:
ImgList = ee.ImageCollection(s1).toList(99999)                                                      # Creates a list of the images to select from
img = ee.Image(ee.List(ImgList).get(1)).select('VV')                                                # Gets the first image to display
img

##4.2 Plot the image on the map

First of all, reload the wreck database incase it has already been used (see above) and extract the lattitude and longitude of the HMS REPULSE and make a `ee.Geometry.Point()` that can be used to centre the map on the wreck at zoom level of 10 (this can be changed to suit any requirement).

Next the image display parameters are defined using `img_params = {'bands':'VV', 'min':-25, 'max':5} ` then extract the date information from the index as not included in a nice easy way to extract from the metadata and finally plot with the date as the layer name.


In [17]:
# Loads the xls file from your personal google drive
Wrecks = pd.read_excel('/content/drive/MyDrive/Wreck Database_V2.3.xls')                            

# Get the position of the wreck
Lat = pd.to_numeric(Wrecks.loc[Wrecks['Wreck_ID'] == 'HMS REPULSE']['Latitude'])                    # Get the latitude of selected wreck
Lon = Wrecks.loc[Wrecks['Wreck_ID'] == 'HMS REPULSE']['Longitude']                                  # Get the longitude of selected wreck
geom = ee.Geometry.Point(Lon.iloc[0],Lat.iloc[0]);                                                  # Loction of chosen wreck

SingleImgMap = geemap.Map()                                                                         # Base map
SingleImgMap.centerObject(geom, 10)                                                                 # Center the map on the wreck
SingleImgMap.add_points_from_xy(Wrecks, x="Longitude", y="Latitude")                                # Add wreck locations

img_params = {'bands':'VV', 'min':-25, 'max':5}                                                     # Selects the VV band and the min and max values to display

# The metadata doesnt have the date, have to extract from image name (called index)
year = ee.Image(img).getString('system:index').slice(-50, 21)                                       # Select out the year
month = ee.Image(img).getString('system:index').slice(-46, 23)                                      # Select out the month
day = ee.Image(img).getString('system:index').slice(-44, 25)                                        # Select out the day
date = ee.String(year.cat('-').cat(month).cat('-').cat(day))                                        # Format to date format e.g. 2023_01_01
date = date.getInfo()                                                                               # ee.String an object on server side so need to extract it

#Visualizing the map
SingleImgMap.addLayer(img, img_params, date,True)                                                   # Adds the image based on parameters defined
SingleImgMap                                                                                        # Display the map

Map(center=[3.620619000000001, 104.34518100000001], controls=(WidgetControl(options=['position', 'transparent_…

## 4.3 Adding a interactive textbox widget to the map
Here is a simple text widget (see section 5.5 for more advanced widgets) that adds a interactive textbox to the bottom right of the map, allowing the user to type the wreck name in. We could extract it from the point layer but thought we might want to explore other wrecks and not be limited to our list and if locations not accurate. This textbox is used to populate the table with the date and size of the spill.

In [18]:
WreckName = widgets.Text(value ='',                                                                 # Blank so we can type over
                         placeholder='Enter a wreck name',                                          # Text to prompt the user
                         description='Wreck:')                                                      # Text in front of the interactive box

WreckNameWidget = ipyleaflet.WidgetControl(widget=WreckName, position='bottomright')                # Method to add to the map
SingleImgMap.add_control(WreckNameWidget)                                                           # Adds the widget to the map

## 4.4 Delineating potential oil spills

From the image there is clearly some potential leak from the two wrecks. This an **important step in determining what is and not oil**. To select out pixels based on a certain thrershold and highlight them you can use the inspector tool to figure out the value of the area of the spills. I have done this and it is roughly -23 or lower. You can use `lt` for lower than and `gt` for greater than and then mask (hide) the other pixels. I then highlighted these pixels in red and renamed the layer *'Pixels < -23'*. 

In [19]:
Oil = (img.lt(-23.5).selfMask().rename('Pixels < -23'))                                               # Selects pixel values less than -23.5
SingleImgMap.addLayer(Oil, {'palette': 'FF0000'}, 'Pixels < -23')                                  # Add mask layer, colour red and rename

## 4.5 Converting raster to vector

Using the smallest pixel value (10 m) then GEE doesnt like it and it can take **along time** so to help speed up and allow the highest resolution, draw a polygon around the oil spills on the above map. 

The below code then extracts it from the map to be used in converting the pixels into rasters `ee.FeatureCollection(SingleImgMap.draw_features)`

In [20]:
AoI = ee.FeatureCollection(SingleImgMap.draw_features)                                              # Extracts the drawn polygon from the map

## 4.6 extracting the oil spill areas
This is **another important step in determing what is and not oil**. Above the pixels were selected but here in the code below **`scale`** is important as refers to the image resolution, in this case the max is 10m. You can play with this and change to 50 or 100 and see each square of polygon become larger. Additionally, the **`maxPixels`** determines the maximum number of pixels GEE can deal with. If you get an error or the polygons dont load you can try increasing this or make the drawn polygon smaller. `Eightconnected`  will include pixels in a polgon if they are connected on a diagonal, include for now.

The following code `Oil_Polygons.filter(ee.Filter.gt('count',25))` is particularly **crucial to determining the extent of any potential oil spills**. This filters the polygons to remove any polygons comprised of 25 pixels or less. This removes alot of the noise, although some small polygons may still exist.

Below the pixels are now grouped and converted to rasters and coloured yellow.

In [21]:
Oil_Polygons = Oil.reduceToVectors(geometry = AoI,                                                  # Polygon extracted from the map
                             scale = 10,                                                            # Resolution of data in meters
                             geometryInNativeProjection =True,                                      # Use the image projection                                 
                             maxPixels = 1e10,                                                      # Max pixels GEE will deal with                                                  
                             eightConnected =True)                                                  # Polgons will count as connect if at a diagonal
Oil_Polygons = Oil_Polygons.filter(ee.Filter.gt('count',25))                                        # Filters the polgons whic have more than 25 pixels

SingleImgMap.addLayer(ee.Image().paint(Oil_Polygons), {'palette': ['F2C80F']}, 'Oil_Polygons', True)# FE6DB6= pink


## 4.7 Extracting the data from the map
To know the area of the oil spill, extract the area of all the polygons then combine it with the date and name of the wreck to export.

In [22]:
spillarea = Oil_Polygons.geometry().area(maxError = 1).getInfo()                                    # Gets the area of the total oil spill
data =[[WreckName.value,date, spillarea]]                                                           # Combine the data together
Datatable = pd.DataFrame(data,columns = ['Wreck_Name', 'Date', 'Oil_Area_m2'])                      # Package as a dataframe
Datatable                                                                                           # View data

Wreck_Name        Date   Oil_Area_m2
0  HMS REPULSE  2015-03-23  3.291114e+07

# 5 Looking through an image collection
Now to look at multiple images, the following code creates a time slider `Map.add_time_slider(imgCollection, vis_params, position='bottomright',time_interval = 3)` but jumps and slow and bit clunky. Instead below we will create our own widgets.


##5.1 Defining input parameters for the image collection using widgets

To investigate a single wreck at a time at the moment so use widgets (not part of the map) to define the parameters. This is populated from the wreck table. Can add as many options here as we need such as date, orbit, wreck name, instrument name etc...

In [4]:
# Loads the xls file from your personal google drive (need to do it each time to create popup correctly)
Wrecks = pd.read_excel('/content/drive/MyDrive/Wreck Database_V2.3.xls') 

WRKdropdown = widgets.Dropdown(options=list(Wrecks.Wreck_ID),                                       # List of the wrecks from our data frame
                            value='HMS REPULSE',                                                    # Default value, here the repulse as one using as an example
                            description='Wreck:')                                                   # Descriptor in front of dropdown

StartDate = widgets.DatePicker(description='Start Date')                                            # Setup the calendar to pick the start date to investigate
EndDate = widgets.DatePicker(description='End Date')                                                # Setup the calendar to pick the end date to investigate
orbit = widgets.Dropdown(options=list(['ASCENDING','DESCENDING']),                                  # List of the wrecks from our data frame
                            value='DESCENDING',                                                     # Default value, here the repulse as one using as an example
                            description='Orbit pass:')                                              # Descriptor in front of dropdown
display(WRKdropdown,StartDate,EndDate,orbit)                                                        # Display the widgets           

Dropdown(description='Wreck:', index=2, options=('SS DERBENT', 'HMS PRINCE OF WALES', 'HMS REPULSE', 'RFA WAR …

DatePicker(value=None, description='Start Date')

DatePicker(value=None, description='End Date')

Dropdown(description='Orbit pass:', index=1, options=('ASCENDING', 'DESCENDING'), value='DESCENDING')

## 5.2 Filtering the image collection
Use the widgets above to select the required images. Use the wreck location to select the only images in locality of the wreck and then filter with with the other widgets. 

In [5]:
# Get the position of the wreck
Lat = pd.to_numeric(Wrecks.loc[Wrecks['Wreck_ID'] == WRKdropdown.value]['Latitude'])                # Get the latitude of selected wreck
Lon = Wrecks.loc[Wrecks['Wreck_ID'] == WRKdropdown.value]['Longitude']                              # Get the longitude of selected wreck
geom = ee.Geometry.Point(Lon.iloc[0],Lat.iloc[0]);                                                  # Loction of chosen wreck

# Get the image collection
ImgCol = (ee.ImageCollection('COPERNICUS/S1_GRD').                                                  # Selects the Sentinel 1 image collection 
  filterDate(str(StartDate.value), str(EndDate.value)).                                             # Selects only the dates from time period chosen above
  filterMetadata('instrumentMode', 'equals', 'IW').                                                 # Selects the instrument mode that we want
  filter(ee.Filter.eq('orbitProperties_pass', str(orbit.value))).                                   # Selects the orbit path we want
  filterBounds(geom))                                                                               # Selects only images that our wreck is contained within

## 5.3 Setting up the imagery to display
To move backwards and forwards through the `ee.ImageCollection` convert it to a list. 

Selects the first image available to display on map startup.
For e.g. the below code will show the first image.

In [6]:
ImgList = ee.ImageCollection(ImgCol).toList(99999)                                                  # Creates a list of the images to select from
ee.Image(ee.List(ImgList).get(1)).select('VV')                                                      # Gets the first image to display
Oil_Polygons = ee.FeatureCollection([])                                                             # Need an empty FeatureCollection to Append our polygons to

##5.4 Display the multimap
Few things happen here:
*   Uses the wreck selected above to centre the map on the wreck and adds the points.
*   Extracts the first image in the image collection.
*   Adds a text widget that uses the extracted time from the image and set ups the conditions to display.
*  Using `with output_widget: print(firstdate)` adds the date to the map and can use later` output_widget.clear_output()` to clear and to allow the date to update.







In [27]:
Oil_Polygons = ee.FeatureCollection([])                                                             # Need an empty FeatureCollection to Append our polygons to, add here so resets

MultiMap = geemap.Map()                                                                             # Base map
MultiMap.centerObject(geom, 10)                                                                     # Center the map on the wreck
MultiMap.add_points_from_xy(Wrecks, x="Longitude", y="Latitude")                                    # Add wreck locations

n = 1                                                                                               # used to add or subtract to change the image
img = ee.Image(ee.List(ImgList).get(n)).select('VV')                                                # Gets the first image to display
year = ee.Image(img).getString('system:index').slice(-50, 21)                                       # Select out the year
month = ee.Image(img).getString('system:index').slice(-46, 23)                                      # Select out the month
day = ee.Image(img).getString('system:index').slice(-44, 25)                                        # Select out the day
firstdate = ee.String(year.cat('-').cat(month).cat('-').cat(day))                                   # Format to date format e.g. 2023_01_01
firstdate = firstdate.getInfo()                                                                     # ee.String an object on server side so need to extract it
                                                                             
img_params = {'bands':'VV', 'min':-25, 'max':5}                                                     # Display setting for the VV band
MultiMap.addLayer(img, img_params, 'Satellite Image',True)                                          # Add the image to the map
output_widget = widgets.Output(layout={'border': '1px solid black'})                                # Set up widget for adding date
output_control = ipyleaflet.WidgetControl(widget=output_widget, position='bottomright')             # Method to add widget
MultiMap.add_control(output_control)                                                                # Adds the widget

with output_widget:                                                                                 # The date widget update
    print(firstdate)                                                                                # Prints the first image date

MultiMap                                                                                            # Display the map

Map(center=[3.620619000000001, 104.34518100000001], controls=(WidgetControl(options=['position', 'transparent_…

## 5.5 Adding control widgets

### 5.51 Detect potential oil widget

This adds the button *Detect potential oil* with the first section creating and adding the widget to the map. The position of the widget can be changed but very limited to corners i.e. topleft, bottomright.

The second part defines the function for what happens when the button is pressed. First of all, if a polygon been drawn it extracts the geometry using  `ee.FeatureCollection(MultiMap.draw_features) `. Secondly, it finds all pixels `lt(-25)` and then adds them to the map in red (`FF0000`) with layer name of `'Pixels < -25'`. 

The third part converts the pixels to polygons for the AoI otherwise it takes alot of comptational time and often doesnt work. Additionally, it filters out any other large objects with similar values. `Scale = 10` refers to the resolution which is 10m. Additionally, the **`maxPixels`** determines the maximum number of pixels GEE can deal with. If you get an error or the polygons dont load, try increasing this or make the drawn polygon smaller. `Eightconnected` will include pixels in a polgon if they connect on a diagonal, included for now.

The following code `Oil_Polygons.filter(ee.Filter.gt('count',25))` filters the polygons to remove any polygons comprised of 25 pixels or less. This removes alot of the noise although some small polygons may still exist. Polygons are then merged with others created from other dates, or the blank `featureCollection` if thefirst image to be analysed.


In [ ]:
DetectOilButton = widgets.Button(description="Detect potential oil")                                # Button widget to add to the map
DetectOilButtonOutput = widgets.Output()                                                            # Output to display for the widget
DetectOilButtonWidget = ipyleaflet.WidgetControl(widget=DetectOilButton, position='bottomright')    # Method to add to the map
MultiMap.add_control(DetectOilButtonWidget)                                                         # Adds to the map

def on_button_clicked(b):                                                                           # Define a function for what happens on button click
  global Oil_Polygons                                                                               # Need this as otherwise it looks internally of the function for value (notsure why)
  with DetectOilButtonOutput:                                                                       # Below happens when button clicked   
   AoI = ee.FeatureCollection(MultiMap.draw_features)                                               # Extracts the drawn polygon from the map
   Oil = (img.lt(-25).selfMask().rename('Pixels < -25'))                                            # Selects pixel values less than -23.5
   MultiMap.addLayer(Oil, {'palette': 'FF0000'}, 'Pixels < -25')                                    # Select those with pixels value 25
   Oil_Polygonstmp = Oil.reduceToVectors(geometry = AoI,                                            # Polygon extracted from the map
                             scale = 10,                                                            # Resolution of data in meters
                             geometryInNativeProjection =True,                                      # Use the image projection                                 
                             maxPixels = 1e10,                                                      # Max pixels GEE will deal with                                                  
                             eightConnected =True)                                                  # Polgons will count as connect if at a diagonal
   Oil_Polygonstmp = Oil_Polygonstmp.filter(ee.Filter.gt('count',25))                               # Filters the polgons whic have more than 25 pixels
   Oil_Polygons = Oil_Polygons.merge(Oil_Polygonstmp)                                               # Merge polygons from each date
   MultiMap.addLayer(ee.Image().paint(Oil_Polygons), {'palette': ['F2C80F']}, 'Oil_Polygons', True) # Adds the polygons FE6DB6= pink
   
DetectOilButton.on_click(on_button_clicked)                                                         # Makes changes when clicked
  

###5.52 Next image widget

This widget is a bit simpler and can be used to navigate through the images. However, if pressed after analysis on the image it will store the polygons and plot the previous detected oil and potentially start to show a pattern.

At the start of the function it removes the last drawn polygon` MultiMap.remove_last_drawn()` so not to clutter the map and removes the date `output_widget.clear_output()` ready to add the date of the next image (later in the code).

To select the next image, 1 is added to our iteration number (`n += 1 `) and used to select from our `ImageCollection` list ( `ee.Image(ee.List(ImgList).get(n)).select('VV')`) note that we are only selecting the `VV` band. The date is extracted from the image and added to the map by updating the widget (described above) whilst adding the next image and any previous oil spill polygons.

In [ ]:
NextButton = widgets.Button(description="Next image")                                               # Button widget to add to the map
NextButtonOutput = widgets.Output()                                                                 # Output to display for the widget
NextButtonWidget = ipyleaflet.WidgetControl(widget=NextButton, position='bottomright')              # Method to add to the map
MultiMap.add_control(NextButtonWidget)                                                              # Adds to the map

def on_button_clicked(b):                                                                           # Define a function for what happens on button click
  ## Operations that need to happen before the button action
  global n                                                                                          # Need this as otherwise it looks internally of the function for value (notsure why)
  global NxtDate                                                                                    # Need this as otherwise it looks internally of the function for value (notsure why)
  global img                                                                                        # Need this as otherwise it looks internally of the function for value (notsure why)
  MultiMap.remove_last_drawn()                                                                      # Removes last drawn polygon
  output_widget.clear_output()                                                                      # Remove display of the date of last image 
  if n == 1: MultiMap.remove_layer(MultiMap.find_layer(firstdate))                                  # If first image (n=1) the removes that
  else: MultiMap.remove_layer(MultiMap.find_layer(NxtDate))                                         # Else removes the one defined in the function
  n += 1                                                                                            # Add one to the number in the image list
  with NextButtonOutput:                                                                            # Below happens when button clicked    
# The metadata doesnt have the date, have to extract from image name (called index)                                                                  
    img = ee.Image(ee.List(ImgList).get(n)).select('VV')                                            # Selects the next image in the list
    year = ee.Image(img).getString('system:index').slice(-50, 21)                                   # Select out the year
    month = ee.Image(img).getString('system:index').slice(-46, 23)                                  # Select out the month
    day = ee.Image(img).getString('system:index').slice(-44, 25)                                    # Select out the day
    NxtDate = ee.String(year.cat('-').cat(month).cat('-').cat(day))                                 # Format to date format e.g. 2023_01_01
    NxtDate = NxtDate.getInfo()                                                                     # ee.String an object on server side so need to extract it
    with output_widget:                                                                             # Method to update date widget
     print(NxtDate)                                                                                 # Updates the image date widget
    MultiMap.addLayer(img, img_params, 'Satellite Image',True)                                      # Add the layer to the map
    MultiMap.addLayer(ee.Image().paint(Oil_Polygons), {'palette': ['F2C80F']}, 'Oil_Polygons', True)# Adds the oil polygons to the map if they exist, FE6DB6= pink
    
NextButton.on_click(on_button_clicked)                                                              # actions the function when the button clicked


spillarea = Oil_Polygons.geometry().area(maxError = 1).getInfo()                                    # Gets the area of the total oil spill
data =[[WreckName.value,date, spillarea]]                                                           # Combine the data together
Datatable = pd.DataFrame(data,columns = ['Wreck_Name', 'Date', 'Oil_Area_m2'])                      # Package as a dataframe


### 5.53 Previous button widget
This widget does the exact same as the one above with the slight difference of `n -= 1 `as it removes 1 from our iteration number. Interestingly, if you press this widget on the first image it will go to the most recent available image.

In [ ]:
PrevButton = widgets.Button(description="Previous image")                                           # Button widget to add to the map
PrevButtonOutput = widgets.Output()                                                                 # Output to display for the widget
PrevButtonWidget = ipyleaflet.WidgetControl(widget=PrevButton, position='bottomleft')               # Method to add to the map
MultiMap.add_control(PrevButtonWidget)                                                              # Adds to the map

def on_button_clicked(b):                                                                           # Define a function for what happens on button click
  ## Operations that need to happen before the button action
  global n                                                                                          # Need this as otherwise it looks internally of the function for value (notsure why)
  global NxtDate                                                                                    # Need this as otherwise it looks internally of the function for value (notsure why)
  if n == 1: MultiMap.remove_layer(MultiMap.find_layer(firstdate))                                  # If first image (n=1) the removes that
  else: MultiMap.remove_layer(MultiMap.find_layer(NxtDate))                                         # Else removes the one defined in the function
  n -= 1                                                                                            # Add one to the number in the image list
  output_widget.clear_output()
  with PrevButtonOutput:                                                                            # Below happens when button clicked    
# The metadata doesnt have the date, have to extract from image name (called index)                                                                  
    img = ee.Image(ee.List(ImgList).get(n)).select('VV')                                            # Selects the next image in the list
    year = ee.Image(img).getString('system:index').slice(-50, 21)                                   # Select out the year
    month = ee.Image(img).getString('system:index').slice(-46, 23)                                  # Select out the month
    day = ee.Image(img).getString('system:index').slice(-44, 25)                                    # Select out the day
    NxtDate = ee.String(year.cat('-').cat(month).cat('-').cat(day))                                 # Format to date format e.g. 2023_01_01
    NxtDate = NxtDate.getInfo()                                                                     # ee.String an object on server side so need to extract it
    with output_widget:
      print(NxtDate)
    MultiMap.addLayer(img, img_params, NxtDate,True)                                                # Add the layer to the map
    MultiMap.addLayer(ee.Image().paint(Oil_Polygons), {'palette': ['F2C80F']}, 'Oil_Polygons', True)# FE6DB6= pink


    
PrevButton.on_click(on_button_clicked)

### 5.6 Growing polygon regions

This does work by adding buffers at 50m and then merging overlapping polygons using `dissolve`. Then convert back to `FeatureCollection` to add to the map.

This takes **ALONG TIME** to run and only for small polygon regions. When have hundreds from speckal it stops working, so another option needs exploring.

In [ ]:
Oil_Polygons4 = Oil_Polygons.geometry().buffer(50)                                                  # Adds a buffer
Oil_Polygons4 = Oil_Polygons4.dissolve()                                                            # Merges the polygons
Oil_Polygons4 = ee.FeatureCollection(Oil_Polygons4)                                                 # Convert back to FeatureCollection
MultiMap.addLayer(ee.Image().paint(Oil_Polygons4), {'palette': ['FE6DB6']}, 'Oil_Polygonsp', True)  # Adds to=he polygons to the map 

## 5.6 All code in one chunk

In [8]:
Oil_Polygons = ee.FeatureCollection([])                                                             # Need an empty FeatureCollection to Append our polygons to, add here so resets

MultiMap = geemap.Map()                                                                             # Base map
MultiMap.centerObject(geom, 10)                                                                     # Center the map on the wreck
MultiMap.add_points_from_xy(Wrecks, x="Longitude", y="Latitude")                                    # Add wreck locations

n = 1                                                                                               # used to add or subtract to change the image
img = ee.Image(ee.List(ImgList).get(n)).select('VV')                                                # Gets the first image to display
year = ee.Image(img).getString('system:index').slice(-50, 21)                                       # Select out the year
month = ee.Image(img).getString('system:index').slice(-46, 23)                                      # Select out the month
day = ee.Image(img).getString('system:index').slice(-44, 25)                                        # Select out the day
firstdate = ee.String(year.cat('-').cat(month).cat('-').cat(day))                                   # Format to date format e.g. 2023_01_01
firstdate = firstdate.getInfo()                                                                     # ee.String an object on server side so need to extract it
                                                                             
img_params = {'bands':'VV', 'min':-25, 'max':5}                                                     # Display setting for the VV band
MultiMap.addLayer(img, img_params, 'Satellite Image',True)                                          # Add the image to the map
output_widget = widgets.Output(layout={'border': '1px solid black'})                                # Set up widget for adding date
output_control = ipyleaflet.WidgetControl(widget=output_widget, position='bottomright')             # Method to add widget
MultiMap.add_control(output_control)                                                                # Adds the widget

with output_widget:                                                                                 # The date widget update
    print(firstdate)                                                                                # Prints the first image date


###################################################################################
DetectOilButton = widgets.Button(description="Detect potential oil")                                # Button widget to add to the map
DetectOilButtonOutput = widgets.Output()                                                            # Output to display for the widget
DetectOilButtonWidget = ipyleaflet.WidgetControl(widget=DetectOilButton, position='bottomright')    # Method to add to the map
MultiMap.add_control(DetectOilButtonWidget)                                                         # Adds to the map

def on_button_clicked(b):                                                                           # Define a function for what happens on button click
  global Oil_Polygons                                                                               # Need to make sure it brings from outside the function
  with DetectOilButtonOutput:                                                                       # Below happens when button clicked   
   AoI = ee.FeatureCollection(MultiMap.draw_features)                                               # Extracts the drawn polygon from the map
   Oil = (img.lt(-25).selfMask().rename('Pixels < 25'))                                              # Selects pixel values less than -23.5
   MultiMap.addLayer(Oil, {'palette': 'FF0000'}, 'Pixels < 25')                                     # Select those with pixels value 25
   Oil_Polygonstmp = Oil.reduceToVectors(geometry = AoI,                                            # Polygon extracted from the map
                             scale = 10,                                                            # Resolution of data in meters
                             geometryInNativeProjection =True,                                      # Use the image projection                                 
                             maxPixels = 1e10,                                                      # Max pixels GEE will deal with                                                  
                             eightConnected =True)                                                  # Polgons will count as connect if at a diagonal
   Oil_Polygonstmp = Oil_Polygonstmp.filter(ee.Filter.gt('count',25))                               # Filters the polgons whic have more than 25 pixels
   Oil_Polygonstmp = Oil_Polygonstmp.set('Img_date', NxtDate)
   Oil_Polygons = Oil_Polygons.merge(Oil_Polygonstmp)                                               # Merge polygons from each date
   MultiMap.addLayer(ee.Image().paint(Oil_Polygons), {'palette': ['F2C80F']}, 'Oil_Polygons', True) # Adds the polygons FE6DB6= pink
   
DetectOilButton.on_click(on_button_clicked)                                                         # Makes changes when clicked
########################################################################################################
NextButton = widgets.Button(description="Next image")                                               # Button widget to add to the map
NextButtonOutput = widgets.Output()                                                                 # Output to display for the widget
NextButtonWidget = ipyleaflet.WidgetControl(widget=NextButton, position='bottomright')              # Method to add to the map
MultiMap.add_control(NextButtonWidget)                                                              # Adds to the map

def on_button_clicked(b):                                                                           # Define a function for what happens on button click
  ## Operations that need to happen before the button action
  global n                                                                                          # Need this as otherwise it looks internally of the function for value (notsure why)
  global NxtDate                                                                                    # Need this as otherwise it looks internally of the function for value (notsure why)
  global img                                                                                        # Need this as otherwise it looks internally of the function for value (notsure why)
  MultiMap.remove_last_drawn()                                                                      # Removes last drawn polygon
  output_widget.clear_output()                                                                      # Remove display of the date of last image 
  if n == 1: MultiMap.remove_layer(MultiMap.find_layer(firstdate))                                  # If first image (n=1) the removes that
  else: MultiMap.remove_layer(MultiMap.find_layer(NxtDate))                                         # Else removes the one defined in the function
  n += 1                                                                                            # Add one to the number in the image list
  with NextButtonOutput:                                                                            # Below happens when button clicked    
  # The metadata doesnt have the date, have to extract from image name (called index)                                                                  
    img = ee.Image(ee.List(ImgList).get(n)).select('VV')                                            # Selects the next image in the list
    year = ee.Image(img).getString('system:index').slice(-50, 21)                                   # Select out the year
    month = ee.Image(img).getString('system:index').slice(-46, 23)                                  # Select out the month
    day = ee.Image(img).getString('system:index').slice(-44, 25)                                    # Select out the day
    NxtDate = ee.String(year.cat('-').cat(month).cat('-').cat(day))                                 # Format to date format e.g. 2023_01_01
    NxtDate = NxtDate.getInfo()                                                                     # ee.String an object on server side so need to extract it
    with output_widget:                                                                             # Method to update date widget
     print(NxtDate)                                                                                 # Updates the image date widget
    MultiMap.addLayer(img, img_params, 'Satellite Image',True)                                      # Add the layer to the map
    MultiMap.addLayer(ee.Image().paint(Oil_Polygons), {'palette': ['F2C80F']}, 'Oil_Polygons', True)# Adds the oil polygons to the map if they exist, FE6DB6= pink
    
NextButton.on_click(on_button_clicked)                                                              # actions the function when the button clicked
############################################################################################################
PrevButton = widgets.Button(description="Previous image")                                           # Button widget to add to the map
PrevButtonOutput = widgets.Output()                                                                 # Output to display for the widget
PrevButtonWidget = ipyleaflet.WidgetControl(widget=PrevButton, position='bottomleft')               # Method to add to the map
MultiMap.add_control(PrevButtonWidget)                                                              # Adds to the map

def on_button_clicked(b):                                                                           # Define a function for what happens on button click
  ## Operations that need to happen before the button action
  global n                                                                                          # Need this as otherwise it looks internally of the function for value (notsure why)
  global NxtDate                                                                                    # Need this as otherwise it looks internally of the function for value (notsure why)
  if n == 1: MultiMap.remove_layer(MultiMap.find_layer(firstdate))                                  # If first image (n=1) the removes that
  else: MultiMap.remove_layer(MultiMap.find_layer(NxtDate))                                         # Else removes the one defined in the function
  n -= 1                                                                                            # Add one to the number in the image list
  output_widget.clear_output()
  with PrevButtonOutput:                                                                            # Below happens when button clicked    
# The metadata doesnt have the date, have to extract from image name (called index)                                                                  
    img = ee.Image(ee.List(ImgList).get(n)).select('VV')                                            # Selects the next image in the list
    year = ee.Image(img).getString('system:index').slice(-50, 21)                                   # Select out the year
    month = ee.Image(img).getString('system:index').slice(-46, 23)                                  # Select out the month
    day = ee.Image(img).getString('system:index').slice(-44, 25)                                    # Select out the day
    NxtDate = ee.String(year.cat('-').cat(month).cat('-').cat(day))                                 # Format to date format e.g. 2023_01_01
    NxtDate = NxtDate.getInfo()                                                                     # ee.String an object on server side so need to extract it
    with output_widget:
      print(NxtDate)
    MultiMap.addLayer(img, img_params, NxtDate,True)                                                # Add the layer to the map
    MultiMap.addLayer(ee.Image().paint(Oil_Polygons), {'palette': ['F2C80F']}, 'Oil_Polygons', True)# FE6DB6= pink


    
PrevButton.on_click(on_button_clicked)
MultiMap                                                                                            # Display the map
                                                                             

Map(center=[3.620619000000001, 104.34518100000001], controls=(WidgetControl(options=['position', 'transparent_…

# 6 Next thing to do
this bit of code below adds the date to the group of polygons. Needs integrating with the widget then each colouring by date.
add slider for pixel value
Also export table 

In [41]:
def addDate(feature):
  return feature.set({'Date': firstdate})
Oil_Polygonstmp2 = Oil_Polygonstmp.map(addDate)

https://www.youtube.com/watch?v=UXHTiqLhsyI

remote sensing training